## финальное:

In [106]:
import pandas as pd
import numpy as np
import geopandas as gpd
import warnings
from shapely import wkt, Polygon, Point
warnings.simplefilter(action='ignore', category=FutureWarning)

## Оценим кластеризацию:

In [107]:
houses_geom = pd.read_csv("hdbscan.csv")

In [113]:
X = houses_geom.drop(columns=['cluster_label', 'CLUSTER_HDBSCAN'])

from sklearn.metrics import davies_bouldin_score, silhouette_score
from sklearn.cluster import KMeans

# Calculate the Davies-Bouldin Index
dbi = davies_bouldin_score(X, houses_geom['cluster_label'])
print("KMEANS - Davies-Bouldin Index:", dbi)
silhouette_avg = silhouette_score(X, houses_geom['cluster_label'])
print("KMEANS - Silhouette Score:", silhouette_avg)

dbi = davies_bouldin_score(X, houses_geom['CLUSTER_HDBSCAN'])
print("HDBSCAN - Davies-Bouldin Index:", dbi)
silhouette_avg = silhouette_score(X, houses_geom['CLUSTER_HDBSCAN'])
print("HDBSCAN - Silhouette Score:", silhouette_avg)

KMEANS - Davies-Bouldin Index: 0.41187054135917367
KMEANS - Silhouette Score: 0.6514462933155907
HDBSCAN - Davies-Bouldin Index: 3.8687133361377914
HDBSCAN - Silhouette Score: 0.6707560610554963


# PLOT

In [109]:
houses_geom = pd.read_csv("houses_clusterized.csv")
houses_geom = gpd.GeoDataFrame(
    houses_geom, geometry=gpd.points_from_xy(houses_geom.lon, houses_geom.lat), crs="EPSG:4326"
)

In [110]:
import plotly.express as px
houses_geom["cluster_label"] = houses_geom["cluster_label"].astype(str)

px.set_mapbox_access_token(open(".mapbox_token").read())
fig = px.scatter_geo(houses_geom,
                     lat=houses_geom.geometry.y,
                     lon=houses_geom.geometry.x,
                     color="cluster_label", # which column to use to set the color of markers
                     projection="natural earth",
                     size_max=0.2)
fig.update_geos(fitbounds="locations")
fig.update_layout(height=1000, margin={"r":0,"t":0,"l":0,"b":0})
fig.show()



In [111]:
import plotly.express as px
import plotly.graph_objects as go
area_predictions = pd.read_csv("predicted.csv")
fig = go.Figure()
fig.add_scatter(x=area_predictions['area_name'], y=area_predictions['population'], name='actual')

fig.add_scatter(x=area_predictions['area_name'], y=area_predictions['hs_ratio_pred'], name='prediction through house_supply')
fig.add_scatter(x=area_predictions['area_name'], y=area_predictions['new_predict'], name='new_prediction')
fig.update_layout(title='Population prediction', xaxis_title='Area', yaxis_title='Population', height=800)
fig.show()